<a href="https://colab.research.google.com/github/lenam2132002/Transformer-Explainability/blob/main1/bert_ex_for_model_6_labels_balance.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!git clone -b main1 https://github.com/lenam2132002/Transformer-Explainability.git

Cloning into 'Transformer-Explainability'...
remote: Enumerating objects: 416, done.
remote: Counting objects: 100% (39/39), done.
remote: Compressing objects: 100% (29/29), done.
remote: Total 416 (delta 16), reused 23 (delta 8), pack-reused 377
Receiving objects: 100% (416/416), 4.38 MiB | 8.41 MiB/s, done.
Resolving deltas: 100% (207/207), done.


In [2]:
!pip install captum

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 13.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 23.7/23.7 MB 55.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 823.6/823.6 kB 70.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.1/14.1 MB 93.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 731.7/731.7 MB 2.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 410.6/410.6 MB 2.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 121.6/121.6 MB 8.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.5/56.5 MB 9.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 124.2/124.2 MB 8.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 196.0/196.0 MB 6.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 166.0/166.0 MB 7.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 99.1/99.1 kB 17.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━

In [3]:
%cd /content/Transformer-Explainability

/content/Transformer-Explainability


In [1]:
from transformers import BertTokenizer
from BERT_explainability.modules.BERT.ExplanationGenerator import Generator
from BERT_explainability.modules.BERT.BertForSequenceClassification import BertForSequenceClassification
from transformers import BertTokenizer
from BERT_explainability.modules.BERT.ExplanationGenerator import Generator
from transformers import AutoTokenizer

from captum.attr import visualization
import torch
from transformers import AutoTokenizer, AutoModelForMaskedLM, AutoModel
from transformers import BertTokenizer, BertModel

d:\miniconda\envs\datn\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
model = BertForSequenceClassification.from_pretrained("jackaduma/SecBERT", num_labels=6).to("cuda")
model.eval()
tokenizer = AutoTokenizer.from_pretrained('jackaduma/SecBERT')
# initialize the explanations generator


classifications = ["000 - Normal", '126 - Path Traversal',
               '242 - Code Injection', '274 - HTTP Verb Tampering',
               '66 - SQL Injection', '88 - OS Command Injection']
explanations = Generator(model)

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at jackaduma/SecBERT and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [6]:
# prompt: connect to gg drive

from google.colab import drive
drive.mount('/content/gdrive')


Mounted at /content/gdrive


In [7]:
checkpoint = torch.load('/content/gdrive/MyDrive/Code_Injection_Dataset/model/SecBert_6labels_balance.pt')

In [8]:
dict = checkpoint['state_dict']
dict1 = dict.copy()
for name in dict.keys():
    name_new = name.replace('bert_model', 'bert')
    dict1[name_new] = dict[name]
    del dict1[name]

In [9]:
dict2 = model.state_dict()
# dict2["bert.embeddings.position_ids"]

In [10]:
dict1["bert.embeddings.position_embeddings.weight"] = dict["bert_model.embeddings.position_embeddings.weight"]
dict1["bert.embeddings.word_embeddings.weight"] = dict["bert_model.embeddings.word_embeddings.weight"]
dict1["classifier.weight"] = dict["linear.weight"]
dict1["classifier.bias"] = dict["linear.bias"]
dict1["bert.embeddings.position_ids"] = dict2["bert.embeddings.position_ids"]

In [11]:
model.load_state_dict(dict1)

<All keys matched successfully>

In [12]:
import pandas as pd

In [13]:
normal = pd.read_csv('/content/gdrive/MyDrive/Code_Injection_Dataset/data_new/000.csv')


In [14]:
count = 0
for index, row in normal.iterrows():
    if index > 10:
        break
    # if index <= 10:
    #     continue
    text_batch = [row['text']]
    encoding = tokenizer(text_batch, return_tensors='pt')
    input_ids = encoding['input_ids'].to("cuda")
    attention_mask = encoding['attention_mask'].to("cuda")
    token_type_ids = encoding['token_type_ids'].to("cuda")
    # true class is positive - 1
    true_class = 0
    # generate an explanation for the input
    expl = explanations.generate_LRP(input_ids=input_ids, attention_mask=attention_mask, start_layer=0)[0]
    # normalize scores
    expl = (expl - expl.min()) / (expl.max() - expl.min())
    # get the model classification
    output = torch.nn.functional.softmax(model(input_ids=input_ids, attention_mask=attention_mask)[0], dim=-1)
    classification = output.argmax(dim=-1).item()
    # get class name
    class_name = classifications[classification]
    print(class_name)
    # if the classification is negative, higher explanation scores are more negative
    # flip for visualization
    if class_name != "000 - Normal":
      expl *= (-1)

    tokens = tokenizer.convert_ids_to_tokens(input_ids.flatten())
    print([(tokens[i], expl[i].item()) for i in range(len(tokens))])
    vis_data_records = [visualization.VisualizationDataRecord(
                                    expl,
                                    output[0][classification],
                                    classification,
                                    true_class,
                                    true_class,
                                    1,
                                    tokens,
                                    1)]
    visualization.visualize_text(vis_data_records)

/usr/local/lib/python3.10/dist-packages/transformers/modeling_utils.py:962: FutureWarning: The `device` argument is deprecated and will be removed in v5 of Transformers.
  warnings.warn(


000 - Normal
[('[CLS]', 0.0), ('get', 0.20346246659755707), ('/', 1.0), ('[SEP]', 0.0)]


/usr/local/lib/python3.10/dist-packages/transformers/modeling_utils.py:962: FutureWarning: The `device` argument is deprecated and will be removed in v5 of Transformers.
  warnings.warn(


000 - Normal
[('[CLS]', 0.0), ('get', 1.0), ('/', 0.24084530770778656), ('blog', 0.05441516265273094), ('/', 0.16046738624572754), ('index', 0.060766175389289856), ('.', 0.01571325957775116), ('php', 0.026790617033839226), ('/', 0.3239235281944275), ('2020', 0.05678250268101692), ('/', 0.30629053711891174), ('04', 0.06332826614379883), ('/', 0.2263936996459961), ('04', 0.03131330758333206), ('/', 0.15061922371387482), ('vol', 0.0038920340593904257), ('##upt', 0.005442600231617689), ('##atu', 0.002349505666643381), ('##m', 0.004455056972801685), ('-', 0.0107196643948555), ('repre', 0.0010470582637935877), ('##hen', 0.0), ('##der', 0.0027689512353390455), ('##it', 0.005032772663980722), ('-', 0.011525902897119522), ('ma', 0.007532334886491299), ('##ior', 0.005774553865194321), ('##es', 0.0066271270625293255), ('-', 0.021854819729924202), ('ab', 0.004407829139381647), ('-', 0.016773521900177002), ('sequ', 0.0037131821736693382), ('##i', 0.013280523009598255), ('-', 0.012285851873457432), 

66 - SQL Injection
[('[CLS]', -0.0), ('get', -0.10455641150474548), ('/', -0.04592742770910263), ('blog', -0.009303351864218712), ('/', -0.05676612630486488), ('xmlrpc', -0.012265663594007492), ('.', -0.0069597079418599606), ('php', -0.0), ('?', -0.09950719028711319), ('rs', -0.30921003222465515), ('##d', -1.0), ('[SEP]', -0.004829986020922661)]


...

000 - Normal
[('[CLS]', 0.0), ('get', 1.0), ('/', 0.6121390461921692), ('blog', 0.06926674395799637), ('/', 0.7410446405410767), ('index', 0.012795109301805496), ('.', 0.06482615321874619), ('php', 0.00966971181333065), ('/', 0.5506611466407776), ('comments', 0.06509840488433838), ('/', 0.31352749466896057), ('feed', 0.0), ('/', 0.6110141277313232), ('[SEP]', 0.19445906579494476)]


000 - Normal
[('[CLS]', 0.0), ('get', 1.0), ('/', 0.6121390461921692), ('blog', 0.06926674395799637), ('/', 0.7410446405410767), ('index', 0.012795109301805496), ('.', 0.06482615321874619), ('php', 0.00966971181333065), ('/', 0.5506611466407776), ('comments', 0.06509840488433838), ('/', 0.31352749466896057), ('feed', 0.0), ('/', 0.6110141277313232), ('[SEP]', 0.19445906579494476)]


000 - Normal
[('[CLS]', 0.0), ('get', 1.0), ('/', 0.1390254646539688), ('blog', 0.018319852650165558), ('/', 0.0971054658293724), ('index', 0.03505751118063927), ('.', 0.007229657378047705), ('php', 0.019003789871931076), ('/', 0.16381871700286865), ('2020', 0.0205677580088377), ('/', 0.13212543725967407), ('04', 0.01635351963341236), ('/', 0.10565084218978882), ('04', 0.009144240990281105), ('/', 0.06820361316204071), ('tempor', 0.0032156335655599833), ('##e', 0.022774286568164825), ('-', 0.01651487499475479), ('od', 0.0), ('##it', 0.003986498806625605), ('-', 0.019903462380170822), ('cup', 0.004285532049834728), ('##idi', 0.0031683959532529116), ('##tate', 0.0009117560111917555), ('-', 0.013385007157921791), ('vol', 0.003701120847836137), ('##upt', 0.0025770768988877535), ('##as', 0.003911699168384075), ('-', 0.020517628639936447), ('la', 0.006066543981432915), ('##uda', 0.0024506619665771723), ('##nt', 0.006845396943390369), ('##ium', 0.0019516851752996445), ('-', 0.0159579049795866

000 - Normal
[('[CLS]', 0.0), ('get', 1.0), ('/', 0.2504890263080597), ('blog', 0.033971451222896576), ('/', 0.18448646366596222), ('index', 0.04327346011996269), ('.', 0.018176395446062088), ('php', 0.015768470242619514), ('/', 0.31390270590782166), ('2020', 0.06278790533542633), ('/', 0.21002301573753357), ('04', 0.06607010960578918), ('/', 0.13312655687332153), ('04', 0.0192499291151762), ('/', 0.09318327903747559), ('hi', 0.001568533363752067), ('##c', 0.008662473410367966), ('-', 0.024382974952459335), ('por', 0.0), ('##ro', 0.0033016728702932596), ('-', 0.04458918794989586), ('nih', 0.001150931348092854), ('##il', 0.0036062789149582386), ('-', 0.02719957008957863), ('non', 0.004314348101615906), ('-', 0.041947100311517715), ('rer', 0.003406394738703966), ('##um', 0.02774154394865036), ('/', 0.49977850914001465), ('[SEP]', 0.11472070962190628)]


000 - Normal
[('[CLS]', 0.0), ('get', 0.6717878580093384), ('/', 0.3983742892742157), ('blog', 0.06711853295564651), ('/', 0.39549553394317627), ('wp', 0.032264694571495056), ('-', 0.08702149242162704), ('content', 0.016746820881962776), ('/', 0.4479871690273285), ('uploads', 0.04370295628905296), ('/', 0.8131027221679688), ('2020', 0.0746840164065361), ('/', 1.0), ('04', 0.03619854524731636), ('/', 0.30509188771247864), ('cro', 0.007713353261351585), ('##pped', 0.006731855683028698), ('-', 0.030194278806447983), ('587', 0.0008383575477637351), ('##d6', 0.0005794964963570237), ('##9f', 0.012785248458385468), ('##7', 0.004284984432160854), ('-', 0.03570396453142166), ('b2', 0.0), ('##e2', 0.0022472229320555925), ('-', 0.030329924076795578), ('363', 0.0009094988345168531), ('##b', 0.00271752942353487), ('-', 0.030466314405202866), ('b7', 0.00014946048031561077), ('##6a', 0.0006237293127924204), ('-', 0.02411084622144699), ('5f', 0.006355442106723785), ('##d0', 0.0038046021945774555), ('#

In [15]:
path_travelsal = pd.read_csv('/content/gdrive/MyDrive/Code_Injection_Dataset/data_new/126.csv')
for index, row in path_travelsal.iterrows():
    if index > 1010:
        break
    if index <= 1000:
        continue
    text_batch = [row['text']]
    encoding = tokenizer(text_batch, return_tensors='pt')
    input_ids = encoding['input_ids'].to("cuda")
    attention_mask = encoding['attention_mask'].to("cuda")
    token_type_ids = encoding['token_type_ids'].to("cuda")
    # true class is positive - 1
    true_class = 0
    # generate an explanation for the input
    expl = explanations.generate_LRP(input_ids=input_ids, attention_mask=attention_mask, start_layer=0)[0]
    # normalize scores
    expl = (expl - expl.min()) / (expl.max() - expl.min())
    # get the model classification
    output = torch.nn.functional.softmax(model(input_ids=input_ids, attention_mask=attention_mask)[0], dim=-1)
    classification = output.argmax(dim=-1).item()
    # get class name
    class_name = classifications[classification]
    print(class_name)
    # if the classification is negative, higher explanation scores are more negative
    # flip for visualization
    if class_name != "000 - Normal":
      expl *= (-1)

    tokens = tokenizer.convert_ids_to_tokens(input_ids.flatten())
    print([(tokens[i], expl[i].item()) for i in range(len(tokens))])
    vis_data_records = [visualization.VisualizationDataRecord(
                                    expl,
                                    output[0][classification],
                                    classification,
                                    true_class,
                                    true_class,
                                    1,
                                    tokens,
                                    1)]
    visualization.visualize_text(vis_data_records)

/usr/local/lib/python3.10/dist-packages/transformers/modeling_utils.py:962: FutureWarning: The `device` argument is deprecated and will be removed in v5 of Transformers.
  warnings.warn(


126 - Path Traversal
[('[CLS]', -0.0), ('get', -0.14662715792655945), ('/', -0.03632242605090141), ('blog', -0.015441149473190308), ('/', -0.026684394106268883), ('index', -0.021691303700208664), ('.', -0.03216765448451042), ('php', -0.03023732267320156), ('/', -0.03962688893079758), ('2020', -0.010862990282475948), ('/', -0.027700679376721382), ('03', -0.016861220821738243), ('/', -0.065150186419487), ('.', -0.22933371365070343), ('.', -0.547918438911438), ('%', -0.0792006403207779), ('2f', -0.10936036705970764), ('.', -0.4352608621120453), ('.', -0.6523048877716064), ('%', -0.09436746686697006), ('2f', -0.07431444525718689), ('.', -0.363724946975708), ('.', -0.6481707096099854), ('%', -0.16022269427776337), ('2f', -0.13636082410812378), ('.', -0.6734146475791931), ('.', -1.0), ('%', -0.16560016572475433), ('2f', -0.13890717923641205), ('.', -0.5418586134910583), ('.', -0.7993583083152771), ('%', -0.1480255275964737), ('2f', -0.13012917339801788), ('.', -0.553753674030304), ('.', -0.6

126 - Path Traversal
[('[CLS]', -0.0), ('get', -0.1366054117679596), ('/', -0.050802018493413925), ('blog', -0.014503037557005882), ('/', -0.11830732226371765), ('.', -0.405579537153244), ('.', -0.6317015290260315), ('%', -0.12106835842132568), ('2f', -0.11828677356243134), ('.', -0.42228731513023376), ('.', -0.6797032952308655), ('%', -0.10906839370727539), ('2f', -0.17842209339141846), ('.', -0.3337792754173279), ('.', -0.5239664316177368), ('%', -0.10012994706630707), ('2f', -0.1386413872241974), ('.', -0.44419312477111816), ('.', -0.6788464784622192), ('%', -0.11863347887992859), ('2f', -0.13734911382198334), ('.', -0.38386857509613037), ('.', -0.6221950054168701), ('%', -0.19249486923217773), ('2f', -0.16795051097869873), ('.', -0.7220542430877686), ('.', -1.0), ('%', -0.18840323388576508), ('2f', -0.16580677032470703), ('.', -0.5323522090911865), ('.', -0.7566531896591187), ('%', -0.16120997071266174), ('2f', -0.14171995222568512), ('.', -0.528446614742279), ('.', -0.628504872322

126 - Path Traversal
[('[CLS]', -0.0), ('get', -0.5182100534439087), ('/', -0.2043961137533188), ('blog', -0.06662391126155853), ('/', -0.1476583480834961), ('index', -0.11212198436260223), ('.', -0.15139786899089813), ('php', -0.09632202982902527), ('/', -0.16972340643405914), ('2020', -0.07125850766897202), ('/', -0.17359650135040283), ('03', -0.05419006943702698), ('/', -0.2875424027442932), ('.', -0.46056243777275085), ('.', -0.8593695163726807), ('%', -0.14754937589168549), ('5c', -0.2669132351875305), ('.', -0.6012099981307983), ('.', -0.8171350359916687), ('%', -0.1667991727590561), ('5c', -0.13408522307872772), ('.', -0.36058518290519714), ('.', -0.577407956123352), ('%', -0.14619380235671997), ('5c', -0.3274320662021637), ('.', -0.5829291343688965), ('.', -1.0), ('%', -0.2167685329914093), ('5c', -0.3808012008666992), ('.', -0.5118231773376465), ('.', -0.8213648200035095), ('%', -0.18784500658512115), ('5c', -0.43969690799713135), ('.', -0.6186527013778687), ('.', -0.895834386

126 - Path Traversal
[('[CLS]', -0.0), ('get', -0.3343812823295593), ('/', -0.21488116681575775), ('blog', -0.05014527961611748), ('/', -0.32419878244400024), ('.', -0.7340139746665955), ('.', -1.0), ('%', -0.21103407442569733), ('5c', -0.2585262358188629), ('.', -0.5231012105941772), ('.', -0.8928781747817993), ('%', -0.16983598470687866), ('5c', -0.2665671706199646), ('.', -0.4940611720085144), ('.', -0.8266700506210327), ('%', -0.1491483449935913), ('5c', -0.29827356338500977), ('.', -0.5422772765159607), ('.', -0.7992992401123047), ('%', -0.18276765942573547), ('5c', -0.1951725333929062), ('.', -0.3456396162509918), ('.', -0.544127345085144), ('%', -0.14636266231536865), ('5c', -0.2871079742908478), ('.', -0.5904505848884583), ('.', -0.9676274657249451), ('%', -0.22902554273605347), ('5c', -0.3290252387523651), ('.', -0.5044289231300354), ('.', -0.7753396034240723), ('%', -0.19228635728359222), ('5c', -0.391880601644516), ('.', -0.6191626191139221), ('.', -0.8620051741600037), ('%'

...

126 - Path Traversal
[('[CLS]', -0.0), ('get', -0.2744220197200775), ('/', -0.07814580947160721), ('blog', -0.0399220809340477), ('/', -0.12978754937648773), ('%', -0.10724498331546783), ('2f', -0.12501634657382965), ('.', -0.29435089230537415), ('.', -0.4296189546585083), ('%', -0.133966326713562), ('2f', -0.13568757474422455), ('.', -0.6153481006622314), ('.', -0.8550469279289246), ('%', -0.15475618839263916), ('2f', -0.1512058973312378), ('.', -0.49979645013809204), ('.', -0.7799006700515747), ('%', -0.15637391805648804), ('2f', -0.1488577425479889), ('.', -0.49765878915786743), ('.', -0.6849717497825623), ('%', -0.18474791944026947), ('2f', -0.15543480217456818), ('.', -0.6243932247161865), ('.', -1.0), ('%', -0.2507273852825165), ('2f', -0.21122445166110992), ('.', -0.5736494064331055), ('.', -0.8056861162185669), ('%', -0.20799435675144196), ('2f', -0.1435765027999878), ('.', -0.7333129048347473), ('.', -0.9601780772209167), ('%', -0.18224158883094788), ('2f', -0.1386366337537765

126 - Path Traversal
[('[CLS]', -0.0), ('get', -0.3610905706882477), ('/', -0.17723704874515533), ('blog', -0.049101103097200394), ('/', -0.12683124840259552), ('index', -0.10709543526172638), ('.', -0.12112297117710114), ('php', -0.06514380127191544), ('/', -0.1306155025959015), ('2020', -0.052571263164281845), ('/', -0.12376998364925385), ('03', -0.03853018209338188), ('/', -0.22338899970054626), ('%', -0.07816148549318314), ('5c', -0.08572221547365189), ('.', -0.30600038170814514), ('.', -0.7220616340637207), ('%', -0.10729475319385529), ('5c', -0.15291143953800201), ('.', -0.33566567301750183), ('.', -0.5749204158782959), ('%', -0.11506733298301697), ('5c', -0.12748554348945618), ('.', -0.39671096205711365), ('.', -0.9020922183990479), ('%', -0.16847895085811615), ('5c', -0.2883748412132263), ('.', -0.5506128072738647), ('.', -0.8489164113998413), ('%', -0.17400725185871124), ('5c', -0.25726619362831116), ('.', -0.5902402997016907), ('.', -1.0), ('%', -0.1871166080236435), ('5c', -

126 - Path Traversal
[('[CLS]', -0.0), ('get', -0.4744992256164551), ('/', -0.22024767100811005), ('blog', -0.055227868258953094), ('/', -0.3077210485935211), ('%', -0.20078657567501068), ('5c', -0.41579192876815796), ('.', -0.4281730651855469), ('.', -0.6733382940292358), ('%', -0.13606901466846466), ('5c', -0.37475600838661194), ('.', -0.6321178674697876), ('.', -1.0), ('%', -0.18842853605747223), ('5c', -0.3156847059726715), ('.', -0.407366007566452), ('.', -0.797056257724762), ('%', -0.1459810435771942), ('5c', -0.3140874207019806), ('.', -0.353440523147583), ('.', -0.5662362575531006), ('%', -0.14420168101787567), ('5c', -0.30909258127212524), ('.', -0.37295204401016235), ('.', -0.7810676097869873), ('%', -0.19933761656284332), ('5c', -0.4578724801540375), ('.', -0.5064194798469543), ('.', -0.7234940528869629), ('%', -0.198172926902771), ('5c', -0.3811063766479492), ('.', -0.5360026955604553), ('.', -0.8221451640129089), ('%', -0.19083325564861298), ('5c', -0.4565943479537964), ('

126 - Path Traversal
[('[CLS]', -0.0), ('get', -0.41064587235450745), ('/', -0.11231084167957306), ('blog', -0.040150437504053116), ('/', -0.08959813416004181), ('index', -0.04668483883142471), ('.', -0.05589519068598747), ('php', -0.08146093785762787), ('/', -0.11365292221307755), ('2020', -0.04028679430484772), ('/', -0.1807195097208023), ('03', -0.03014044091105461), ('/', -0.11346090584993362), ('22', -0.15888270735740662), ('/', -0.22352291643619537), ('.', -0.435787558555603), ('.', -0.9575697183609009), ('%', -0.2804759442806244), ('2f', -0.2598855793476105), ('.', -0.6714727282524109), ('.', -0.9104099869728088), ('%', -0.3367258906364441), ('2f', -0.24124082922935486), ('.', -0.6240720748901367), ('.', -1.0), ('%', -0.2687850892543793), ('2f', -0.2323259562253952), ('.', -0.43587154150009155), ('.', -0.5812939405441284), ('%', -0.14677037298679352), ('2f', -0.10950273275375366), ('.', -0.4441259205341339), ('.', -0.5425432920455933), ('%', -0.10842811316251755), ('2f', -0.0860

126 - Path Traversal
[('[CLS]', -0.0), ('get', -0.39175546169281006), ('/', -0.1080624908208847), ('blog', -0.031482670456171036), ('/', -0.08631463348865509), ('index', -0.04762907698750496), ('.', -0.055814821273088455), ('php', -0.06834426522254944), ('/', -0.10428103059530258), ('2020', -0.04305211827158928), ('/', -0.15244832634925842), ('03', -0.035829681903123856), ('/', -0.10426043719053268), ('22', -0.156123086810112), ('/', -0.21010375022888184), ('%', -0.09197524935007095), ('2f', -0.18403935432434082), ('.', -0.6116234660148621), ('.', -0.9909682869911194), ('%', -0.19392749667167664), ('2f', -0.21869219839572906), ('.', -0.6426909565925598), ('.', -0.829428493976593), ('%', -0.26761674880981445), ('2f', -0.26076439023017883), ('.', -0.7899211049079895), ('.', -1.0), ('%', -0.20015540719032288), ('2f', -0.1578107625246048), ('.', -0.4893285036087036), ('.', -0.6597190499305725), ('%', -0.13160286843776703), ('2f', -0.10313309729099274), ('.', -0.3924439251422882), ('.', -0.

In [16]:
code_injection = pd.read_csv('/content/gdrive/MyDrive/Code_Injection_Dataset/data_new/242.csv')
for index, row in code_injection.iterrows():
    if index > 10:
        break
    # if index <= 1000:
    #     continue
    text_batch = [row['text']]
    encoding = tokenizer(text_batch, return_tensors='pt')
    input_ids = encoding['input_ids'].to("cuda")
    attention_mask = encoding['attention_mask'].to("cuda")
    token_type_ids = encoding['token_type_ids'].to("cuda")
    # true class is positive - 1
    true_class = 0
    # generate an explanation for the input
    expl = explanations.generate_LRP(input_ids=input_ids, attention_mask=attention_mask, start_layer=0)[0]
    # normalize scores
    expl = (expl - expl.min()) / (expl.max() - expl.min())
    # get the model classification
    output = torch.nn.functional.softmax(model(input_ids=input_ids, attention_mask=attention_mask)[0], dim=-1)
    classification = output.argmax(dim=-1).item()
    # get class name
    class_name = classifications[classification]
    print(class_name)
    # if the classification is negative, higher explanation scores are more negative
    # flip for visualization
    if class_name != "000 - Normal":
      expl *= (-1)

    tokens = tokenizer.convert_ids_to_tokens(input_ids.flatten())
    print([(tokens[i], expl[i].item()) for i in range(len(tokens))])
    vis_data_records = [visualization.VisualizationDataRecord(
                                    expl,
                                    output[0][classification],
                                    classification,
                                    true_class,
                                    true_class,
                                    1,
                                    tokens,
                                    1)]
    visualization.visualize_text(vis_data_records)

/usr/local/lib/python3.10/dist-packages/transformers/modeling_utils.py:962: FutureWarning: The `device` argument is deprecated and will be removed in v5 of Transformers.
  warnings.warn(


242 - Code Injection
[('[CLS]', -0.0), ('post', -1.0), ('/', -0.04142208769917488), ('vendor', -0.025029875338077545), ('/', -0.042954474687576294), ('php', -0.07341703772544861), ('##unit', -0.029734807088971138), ('/', -0.09001463651657104), ('php', -0.047315213829278946), ('##unit', -0.032345302402973175), ('/', -0.028734320774674416), ('src', -0.034958142787218094), ('/', -0.02293761633336544), ('util', -0.024220386520028114), ('/', -0.028643213212490082), ('php', -0.03076012246310711), ('/', -0.01669388636946678), ('eval', -0.062323037534952164), ('-', -0.008895548060536385), ('stdin', -0.0), ('.', -0.003007161431014538), ('php', -0.0310051366686821), ('<', -0.20448239147663116), ('?', -0.0540638267993927), ('=', -0.020594915375113487), ('md5', -0.06675924360752106), ('(', -0.04111802205443382), ('"', -0.015804149210453033), ('php', -0.025227747857570648), ('##unit', -0.012750397436320782), ('"', -0.17630445957183838), (')', -0.20988106727600098), ('?', -0.5308193564414978), ('>',

242 - Code Injection
[('[CLS]', -0.0), ('post', -0.03481980413198471), ('/', -0.11258622258901596), ('?', -0.08827222883701324), ('-', -0.1577683687210083), ('d', -0.1386687159538269), ('+', -0.14275774359703064), ('allow', -0.02985570579767227), ('_', -0.03438996896147728), ('url', -0.015109634026885033), ('_', -0.07302963733673096), ('include', -0.05479798838496208), ('%', -0.4343928098678589), ('3d', -0.031126676127314568), ('##1', -0.023177234455943108), ('+', -0.18780645728111267), ('-', -0.08695019036531448), ('d', -0.07339072972536087), ('+', -0.11556610465049744), ('auto', -0.02306436002254486), ('_', -0.018729297444224358), ('prepend', -0.0024856540840119123), ('_', -0.04408883675932884), ('file', -0.033108897507190704), ('%', -1.0), ('3d', -0.06994633376598358), ('##php', -0.015294626355171204), (':', -0.008981676772236824), ('/', -0.03720586374402046), ('/', -0.030638691037893295), ('input', -0.028084520250558853), ('<', -0.19948551058769226), ('?', -0.07246271520853043), ('

242 - Code Injection
[('[CLS]', -0.0), ('get', -0.05299460515379906), ('/', -0.039726078510284424), ('?', -0.4699625074863434), ('p4', -0.0384799987077713), ('##yl', -0.008009924553334713), ('##04', -0.1237793043255806), ('##d3', -0.024841642007231712), ('=', -0.15422910451889038), ('<', -0.47401875257492065), ('script', -0.03627161309123039), ('>', -0.14443029463291168), ('alert', -0.11486634612083435), ('(', -0.031697388738393784), ('document', -0.0044677066616714), ('.', -0.0), ('cookie', -0.048614080995321274), (')', -0.7750924825668335), ('<', -1.0), ('/', -0.05553307384252548), ('script', -0.0009907750645652413), ('>', -0.08249849081039429), ('[SEP]', -0.007417119573801756)]


242 - Code Injection
[('[CLS]', -0.0), ('get', -0.0369768887758255), ('/', -0.04466388002038002), ('index', -0.11937516182661057), ('.', -0.021492576226592064), ('php', -0.025464674457907677), ('?', -0.13506199419498444), ('s', -0.09044451266527176), ('=', -0.10946761071681976), ('/', -0.0476444847881794), ('index', -0.029274463653564453), ('/', -0.042064666748046875), ('\\', -0.016611482948064804), ('x5', -0.0017520118271932006), ('##ct', -0.0016168201109394431), ('##hink', -0.0005012810579501092), ('\\', -0.011076853610575199), ('x5', -0.0), ('##cap', -0.002054136712104082), ('##p', -0.006812707055360079), ('/', -0.021693449467420578), ('invoke', -0.015494577586650848), ('##function', -0.06014000251889229), ('&', -0.010106991976499557), ('function', -0.005046821665018797), ('=', -0.010820160619914532), ('call', -0.0016944312956184149), ('_', -0.0021882120054215193), ('user', -0.0007206776645034552), ('_', -0.003056806046515703), ('func', -0.0036778650246560574), ('_', -0.001929613645

...

88 - OS Command Injection
[('[CLS]', -0.0), ('post', -0.14139607548713684), ('/', -0.022158648818731308), ('blog', -0.022806990891695023), ('/', -0.010982360690832138), ('index', -0.014956071972846985), ('.', -0.014358198270201683), ('php', -0.009257759898900986), ('/', -0.011281998828053474), ('my', -0.02212543971836567), ('-', -0.008497344329953194), ('account', -0.018504517152905464), ('/', -0.003274705493822694), ('edit', -0.00521031254902482), ('-', -0.004415889270603657), ('password', -0.020766856148838997), ('/', -0.010647187009453773), ('password', -0.02577645517885685), ('_', -0.0708092749118805), ('current', -0.039252765476703644), ('=', -0.09771616756916046), ('tn', -0.025589589029550552), ('##ce', -0.01281448919326067), ('##qi', -0.008360834792256355), ('##u', -0.01321194227784872), ('&', -0.0445818230509758), ('password', -0.039425384253263474), ('_', -0.09456094354391098), ('1', -0.09641551971435547), ('=', -0.5057488679885864), ('%', -1.0), ('3c', -0.14170458912849426), 

242 - Code Injection
[('[CLS]', -0.0), ('post', -0.15268263220787048), ('/', -0.09032899886369705), ('blog', -0.053716469556093216), ('/', -0.07651633024215698), ('index', -0.051854055374860764), ('.', -0.030143525451421738), ('php', -0.016277337446808815), ('/', -0.037975698709487915), ('my', -0.018516160547733307), ('-', -0.019218439236283302), ('account', -0.013527835719287395), ('/', -0.024334723129868507), ('edit', -0.0038232626393437386), ('-', -0.021734492853283882), ('password', -0.009464140050113201), ('/', -0.01439964585006237), ('password', -0.01296654250472784), ('_', -0.025875931605696678), ('current', -0.01689005084335804), ('=', -0.08126378804445267), ('ec', -0.04640189930796623), ('##fl', -0.026066210120916367), ('##bd', -0.017654167488217354), ('&', -0.012192157097160816), ('password', -0.025536319240927696), ('_', -0.04142862185835838), ('1', -0.013220061548054218), ('=', -0.15543198585510254), ('%', -0.6883621215820312), ('22', -0.46187853813171387), ('%', -0.5846266

88 - OS Command Injection
[('[CLS]', -0.0), ('post', -0.006485724821686745), ('/', -0.00415691128000617), ('blog', -0.0014598278794437647), ('/', -0.0025680847465991974), ('index', -0.003295380622148514), ('.', -0.0033584991469979286), ('php', -0.010266263969242573), ('/', -0.005431394558399916), ('my', -0.024234004318714142), ('-', -0.00661665853112936), ('account', -0.02224522829055786), ('/', -0.0013364898040890694), ('edit', -0.0062188454903662205), ('-', -0.002992018824443221), ('password', -0.018715713173151016), ('/', -0.010254024527966976), ('password', -0.02011210098862648), ('_', -0.04663906618952751), ('current', -0.03707030415534973), ('=', -0.09647093713283539), ('dv', -0.013236898928880692), ('##sz', -0.005889600142836571), ('##g', -0.017709216102957726), ('&', -0.026321908459067345), ('password', -0.027820240706205368), ('_', -0.06563890725374222), ('1', -0.037264734506607056), ('=', -0.1151147335767746), ('dv', -0.01745106466114521), ('##sz', -0.014258465729653835), ('#

242 - Code Injection
[('[CLS]', -0.0), ('post', -0.02643575333058834), ('/', -0.01828021928668022), ('blog', -0.010198169387876987), ('/', -0.011862833984196186), ('index', -0.0055697220377624035), ('.', -0.009725787676870823), ('php', -0.0024345251731574535), ('/', -0.015809033066034317), ('my', -0.004602390807121992), ('-', -0.004954359494149685), ('account', -0.004530453123152256), ('/', -0.011578749865293503), ('edit', -0.001994034741073847), ('-', -0.0035242224112153053), ('password', -0.005716115701943636), ('/', -0.005613739136606455), ('password', -0.006833964493125677), ('_', -0.0030105942860245705), ('current', -0.0023157107643783092), ('=', -0.017606910318136215), ('qb', -0.010056925006210804), ('##iw', -0.00515879737213254), ('##fy', -0.003325920319184661), ('&', -0.005213832017034292), ('password', -0.008793514221906662), ('_', -0.0057935225777328014), ('1', -0.0038472278974950314), ('=', -0.022700849920511246), ('qb', -0.030849002301692963), ('##iw', -0.012521849945187569

242 - Code Injection
[('[CLS]', -0.0), ('post', -0.05618922412395477), ('/', -0.03446390479803085), ('blog', -0.010017823427915573), ('/', -0.030459821224212646), ('index', -0.010253856889903545), ('.', -0.051184047013521194), ('php', -0.008644752204418182), ('/', -0.02157375030219555), ('my', -0.028484467417001724), ('-', -0.011663452722132206), ('account', -0.0024086444173008204), ('/', -0.017434317618608475), ('edit', -0.0047124712727963924), ('-', -0.01139073260128498), ('password', -0.01009410060942173), ('/', -0.016617566347122192), ('password', -0.015711713582277298), ('_', -0.006206994876265526), ('current', -0.0012709947768598795), ('=', -0.026137398555874825), ('fb', -0.008003873750567436), ('##8f', -0.0005855438648723066), ('-', -0.011385797522962093), ('es', -0.006900003645569086), ('&', -0.0263059139251709), ('password', -0.010310856625437737), ('_', -0.008162868209183216), ('1', -0.008057181723415852), ('=', -0.01202909555286169), ('fb', -0.0027689540293067694), ('##8f', 

In [17]:
HTTP_Verb_Tampering = pd.read_csv('/content/gdrive/MyDrive/Code_Injection_Dataset/data_new/274.csv')
for index, row in HTTP_Verb_Tampering.iterrows():
    if index > 10:
        break
    # if index <= 1000:
    #     continue
    text_batch = [row['text']]
    encoding = tokenizer(text_batch, return_tensors='pt')
    input_ids = encoding['input_ids'].to("cuda")
    attention_mask = encoding['attention_mask'].to("cuda")
    token_type_ids = encoding['token_type_ids'].to("cuda")
    # true class is positive - 1
    true_class = 0
    # generate an explanation for the input
    expl = explanations.generate_LRP(input_ids=input_ids, attention_mask=attention_mask, start_layer=0)[0]
    # normalize scores
    expl = (expl - expl.min()) / (expl.max() - expl.min())
    # get the model classification
    output = torch.nn.functional.softmax(model(input_ids=input_ids, attention_mask=attention_mask)[0], dim=-1)
    classification = output.argmax(dim=-1).item()
    # get class name
    class_name = classifications[classification]
    print(class_name)
    # if the classification is negative, higher explanation scores are more negative
    # flip for visualization
    if class_name != "000 - Normal":
      expl *= (-1)

    tokens = tokenizer.convert_ids_to_tokens(input_ids.flatten())
    print([(tokens[i], expl[i].item()) for i in range(len(tokens))])
    vis_data_records = [visualization.VisualizationDataRecord(
                                    expl,
                                    output[0][classification],
                                    classification,
                                    true_class,
                                    true_class,
                                    1,
                                    tokens,
                                    1)]
    visualization.visualize_text(vis_data_records)

274 - HTTP Verb Tampering
[('[CLS]', -0.0), ('th', -0.570431113243103), ('##b', -0.11740868538618088), ('##q', -0.23139792680740356), ('/', -1.0), ('nan', -0.14622512459754944), ('[SEP]', -0.0)]


/usr/local/lib/python3.10/dist-packages/transformers/modeling_utils.py:962: FutureWarning: The `device` argument is deprecated and will be removed in v5 of Transformers.
  warnings.warn(


274 - HTTP Verb Tampering
[('[CLS]', -0.0), ('track', -0.8275437355041504), ('/', -1.0), ('19', -0.005190382711589336), ('##sa', -0.0007369517697952688), ('##q', -0.0), ('nan', -0.03726717457175255), ('[SEP]', -0.015495388768613338)]


274 - HTTP Verb Tampering
[('[CLS]', -0.0), ('track', -1.0), ('/', -0.827223539352417), ('icons', -0.06775500625371933), ('##vc', -0.013628331013023853), ('##cb', -0.0), ('##m', -0.030767032876610756), ('nan', -0.04110317677259445), ('[SEP]', -0.04742660000920296)]


274 - HTTP Verb Tampering
[('[CLS]', -0.0), ('track', -0.8229643702507019), ('/', -1.0), ('icons', -0.18274043500423431), ('/', -0.6053268313407898), ('ubuntu', -0.028128068894147873), ('-', -0.01618519052863121), ('logo', -0.028866397216916084), ('.', -0.0055284951813519), ('png', -0.013142790645360947), ('##yp', -0.0), ('##g', -0.014866812154650688), ('##dk', -0.0015300458762794733), ('nan', -0.019384533166885376), ('[SEP]', -0.01898185722529888)]


...

274 - HTTP Verb Tampering
[('[CLS]', -0.0), ('connect', -1.0), ('www', -0.6060617566108704), ('.', -0.06664253026247025), ('google', -0.04489939287304878), ('.', -0.003080635331571102), ('com', -0.02380906045436859), (':', -0.047109898179769516), ('80', -0.055379368364810944), ('nan', -0.05569257214665413), ('[SEP]', -0.0)]


274 - HTTP Verb Tampering
[('[CLS]', -0.0), ('patch', -0.6759241819381714), ('/', -1.0), ('r4', -0.02980145998299122), ('##ac', -0.06115609407424927), ('##oj', -0.004610550124198198), ('##rv', -0.009709998033940792), ('##8e', -0.003422969486564398), ('"', -0.02290165238082409), ('c8', -0.015603316016495228), ('##ti', -0.004117944743484259), ('##k', -0.01353732030838728), ('##q', -0.001996105769649148), ('##2c', -0.007955732755362988), ('##fg', -0.000840422697365284), ('##ux', -0.0), ('##e8', -0.006432554218918085), ('##1', -0.012020440772175789), ('"', -0.03967509791254997), (':', -0.009779662825167179), ('"', -0.008595280349254608), ('1', -0.000980597105808556), ('##if', -0.001518729142844677), ('##uo', -0.000775849970523268), ('##e8', -0.003812080482020974), ('##rq', -0.0003550677793100476), ('##ds', -0.0014048322336748242), ('##ake', -0.0009082307806238532), ('##t', -0.001488387817516923), ('"', -0.006690151058137417), ('[SEP]', -0.00703179556876421)]


274 - HTTP Verb Tampering
[('[CLS]', -0.0), ('connect', -1.0), ('www', -0.6060617566108704), ('.', -0.06664253026247025), ('google', -0.04489939287304878), ('.', -0.003080635331571102), ('com', -0.02380906045436859), (':', -0.047109898179769516), ('80', -0.055379368364810944), ('nan', -0.05569257214665413), ('[SEP]', -0.0)]


274 - HTTP Verb Tampering
[('[CLS]', -0.0), ('put', -0.7578150033950806), ('/', -1.0), ('ix', -0.08897437900304794), ('##q6', -0.014569258317351341), ('##1', -0.008723191916942596), ('##piv', -0.012525588274002075), ('##7', -0.009015504270792007), ('##k', -0.019440321251749992), ('"', -0.020545680075883865), ('b8', -0.012341952882707119), ('##1b', -0.005288971588015556), ('##aj', -0.005663461983203888), ('##hf', -0.012774582952260971), ('##x', -0.009884389117360115), ('##z', -0.004503096919506788), ('##gw', -0.001123628462664783), ('##ams', -0.013617460615932941), ('"', -0.024630257859826088), (':', -0.04086684808135033), ('"', -0.009812464006245136), ('lb', -0.0052180420607328415), ('##4j', -0.02011781558394432), ('##3', -0.0), ('##jl', -0.0034494714345782995), ('##x', -0.005394541658461094), ('##3z', -0.0009534510318189859), ('##p', -0.004768898710608482), ('##g', -0.002481297589838505), ('##9', -0.004019357264041901), ('##p', -0.002137538744136691), ('##7', -0.0027216786984354258), 

274 - HTTP Verb Tampering
[('[CLS]', -0.0), ('patch', -1.0), ('/', -0.7954363226890564), ('icons', -0.1656942069530487), ('/', -0.39207571744918823), ('r6', -0.017293540760874748), ('##b20', -0.006179374177008867), ('##g2', -0.001975544961169362), ('##2v', -0.0016156710917130113), ('##3', -0.00220959959551692), ('"', -0.008132982067763805), ('kj', -0.0027076483238488436), ('##0', -0.0032157970126718283), ('##je', -0.0007220222032628953), ('##mpi', -0.010891938582062721), ('##ch', -0.0013843452325090766), ('##nn', -0.0028424968477338552), ('##6', -0.0011321522761136293), ('##ku', -0.004829416982829571), ('"', -0.028047092258930206), (':', -0.006002707406878471), ('"', -0.004780723247677088), ('ji', -0.001432261080481112), ('##fp', -0.0), ('##g', -0.003413175931200385), ('##vm', -0.006091051734983921), ('##xa', -0.006728192791342735), ('##ez', -0.0013074917951598763), ('##xq', -0.0004776340792886913), ('##s', -0.0012048877542838454), ('##v', -0.003482363186776638), ('"', -0.0031335749663

In [18]:
sqli = pd.read_csv('/content/gdrive/MyDrive/Code_Injection_Dataset/data_new/66.csv')
for index, row in sqli.iterrows():
    if index > 10:
        break
    # if index <= 1000:
    #     continue
    text_batch = [row['text']]
    encoding = tokenizer(text_batch, return_tensors='pt')
    input_ids = encoding['input_ids'].to("cuda")
    attention_mask = encoding['attention_mask'].to("cuda")
    token_type_ids = encoding['token_type_ids'].to("cuda")
    # true class is positive - 1
    true_class = 0
    # generate an explanation for the input
    expl = explanations.generate_LRP(input_ids=input_ids, attention_mask=attention_mask, start_layer=0)[0]
    # normalize scores
    expl = (expl - expl.min()) / (expl.max() - expl.min())
    # get the model classification
    output = torch.nn.functional.softmax(model(input_ids=input_ids, attention_mask=attention_mask)[0], dim=-1)
    classification = output.argmax(dim=-1).item()
    # get class name
    class_name = classifications[classification]
    print(class_name)
    # if the classification is negative, higher explanation scores are more negative
    # flip for visualization
    if class_name != "000 - Normal":
      expl *= (-1)

    tokens = tokenizer.convert_ids_to_tokens(input_ids.flatten())
    print([(tokens[i], expl[i].item()) for i in range(len(tokens))])
    vis_data_records = [visualization.VisualizationDataRecord(
                                    expl,
                                    output[0][classification],
                                    classification,
                                    true_class,
                                    true_class,
                                    1,
                                    tokens,
                                    1)]
    visualization.visualize_text(vis_data_records)

66 - SQL Injection
[('[CLS]', -0.0), ('get', -0.17272129654884338), ('/', -0.13449254631996155), ('blog', -0.02920173667371273), ('/', -0.21954338252544403), ('index', -0.028216511011123657), ('.', -0.008623436093330383), ('php', -0.009255838580429554), ('/', -0.22592522203922272), ('2020', -0.07285906374454498), ('/', -0.2581155300140381), ('04', -0.2356618195772171), ('%', -0.45161449909210205), ('27', -1.0), ('+', -0.596139669418335), ('and', -0.3218630850315094), ('+', -0.6779934763908386), ('0', -0.4092291295528412), ('+', -0.8112356662750244), ('in', -0.2756422460079193), ('+', -0.9594918489456177), ('%', -0.3405400216579437), ('28', -0.4700057804584503), ('##select', -0.042656026780605316), ('+', -0.4835534691810608), ('sleep', -0.12289910763502121), ('%', -0.21620424091815948), ('2815', -0.12764860689640045), ('%', -0.16630466282367706), ('29', -0.22191102802753448), ('+', -0.6417970657348633), ('%', -0.17105789482593536), ('29', -0.6254465579986572), ('+', -0.5031479001045227)

/usr/local/lib/python3.10/dist-packages/transformers/modeling_utils.py:962: FutureWarning: The `device` argument is deprecated and will be removed in v5 of Transformers.
  warnings.warn(


66 - SQL Injection
[('[CLS]', -0.0), ('get', -0.13823367655277252), ('/', -0.1410224288702011), ('blog', -0.021197957918047905), ('/', -0.3592560589313507), ('index', -0.004414533730596304), ('.', -0.0028890003450214863), ('php', -0.008562499657273293), ('%', -0.5867085456848145), ('2522', -0.1816088855266571), ('%', -0.32123634219169617), ('2b', -0.5637842416763306), ('##and', -0.05206716060638428), ('%', -0.29597440361976624), ('2b', -0.7954834699630737), ('%', -0.21314264833927155), ('2522', -0.02701750211417675), ('##1', -0.02806229516863823), ('%', -0.3159475028514862), ('2522', -0.06012142449617386), ('%', -0.1565616875886917), ('253', -0.045330729335546494), ('##d', -0.0243070051074028), ('%', -0.11301770061254501), ('2522', -0.012917962856590748), ('##2', -0.01116710714995861), ('%', -0.20929047465324402), ('2522', -0.028988655656576157), ('%', -0.0739673301577568), ('2b', -0.0900527760386467), ('-', -0.0036385490093380213), ('-', -0.004599102307111025), ('%', -0.06156759709119

66 - SQL Injection
[('[CLS]', -0.0), ('get', -0.25061944127082825), ('/', -0.4233442544937134), ('blog', -0.0482475608587265), ('/', -0.517261266708374), ('index', -0.0788477435708046), ('.', -0.01571113057434559), ('php', -0.03323177993297577), ('/', -0.3892243802547455), ('2020', -0.13171537220478058), ('/', -0.4207835793495178), ('03', -0.2973880469799042), ('+', -0.964329719543457), ('union', -0.3222823739051819), ('+', -0.9712981581687927), ('all', -0.4413641691207886), ('+', -0.7079848647117615), ('select', -0.2648283541202545), ('+', -1.0), ('null', -0.9493333101272583), ('%', -0.5040478706359863), ('2c', -0.2057032436132431), ('##null', -0.07066217064857483), ('%', -0.3344501256942749), ('2c', -0.2047441303730011), ('##null', -0.06078830361366272), ('%', -0.273867666721344), ('2c', -0.08926060050725937), ('##null', -0.00889682862907648), ('%', -0.07825631648302078), ('2c', -0.0459396131336689), ('##null', -0.01672486774623394), ('%', -0.11314153671264648), ('2c', -0.09482548385

66 - SQL Injection
[('[CLS]', -0.0), ('get', -0.04397953674197197), ('/', -0.20809194445610046), ('blog', -0.000620827020611614), ('/', -0.3640408515930176), ('index', -0.0), ('.', -0.0007048717816360295), ('php', -0.0012053016107529402), ('%', -0.42498573660850525), ('26', -0.0366748683154583), ('##sl', -0.009232301265001297), ('##ee', -0.0012636043829843402), ('##p', -0.04075609892606735), ('%', -0.29908424615859985), ('24', -0.16436849534511566), ('##mc', -0.05064760521054268), ('+', -1.0), ('15', -0.963914692401886), ('%', -0.3115372955799103), ('26', -0.09331221878528595), ('/', -0.36729979515075684), ('2020', -0.0008628797950223088), ('/', -0.2291645109653473), ('04', -0.0017444059485569596), ('/', -0.12269143760204315), ('04', -0.0009348747553303838), ('/', -0.026893511414527893), ('page', -0.00033866948797367513), ('/', -0.0022219091188162565), ('2', -0.0017931379843503237), ('[SEP]', -0.0012942813336849213)]


...

66 - SQL Injection
[('[CLS]', -0.0), ('get', -0.1806936413049698), ('/', -0.15113520622253418), ('blog', -0.07587555795907974), ('%', -0.33304306864738464), ('22', -0.6471925377845764), ('+', -0.5606346130371094), ('or', -0.21184475719928741), ('+', -0.6759758591651917), ('0', -0.3010099232196808), ('+', -0.7014415860176086), ('in', -0.19526782631874084), ('+', -1.0), ('%', -0.3404090404510498), ('28', -0.5032408237457275), ('##select', -0.0425647497177124), ('+', -0.6006532907485962), ('sleep', -0.18531064689159393), ('%', -0.30877551436424255), ('2815', -0.194644033908844), ('%', -0.2591240108013153), ('29', -0.49305614829063416), ('+', -0.6227444410324097), ('%', -0.2124018669128418), ('29', -0.5818919539451599), ('+', -0.43571045994758606), ('-', -0.05745319649577141), ('-', -0.07738298922777176), ('+', -0.4816848635673523), ('/', -0.15921743214130402), ('wp', -0.0041871746070683), ('-', -0.011464365758001804), ('content', -0.00520211411640048), ('/', -0.06507690995931625), ('uploa

66 - SQL Injection
[('[CLS]', -0.0), ('get', -0.09097989648580551), ('/', -0.9430354833602905), ('blog', -0.018757952377200127), ('%', -0.8238012194633484), ('26', -0.050669148564338684), ('##sl', -0.010164604522287846), ('##ee', -0.0017912776675075293), ('##p', -0.032038651406764984), ('%', -0.2653062343597412), ('24', -0.1677059531211853), ('##mc', -0.06803663074970245), ('+', -1.0), ('15', -0.3536890745162964), ('%', -0.4020554721355438), ('26', -0.0936819538474083), ('/', -0.2522871494293213), ('wp', -0.0001503289386164397), ('-', -2.8654019843088463e-05), ('includes', -0.0002919052785728127), ('/', -0.02688228338956833), ('css', -0.0), ('[SEP]', -0.00909256562590599)]


66 - SQL Injection
[('[CLS]', -0.0), ('get', -0.22093604505062103), ('/', -0.1790725439786911), ('blog', -0.04291754215955734), ('/', -0.2441665530204773), ('index', -0.044580522924661636), ('.', -0.013656987808644772), ('php', -0.03497057408094406), ('%', -0.3940086364746094), ('27', -0.851702868938446), ('+', -0.6223524808883667), ('or', -0.3110474646091461), ('+', -0.9546072483062744), ('0', -0.554729700088501), ('+', -0.9502409100532532), ('in', -0.29719898104667664), ('+', -1.0), ('%', -0.4552227854728699), ('28', -0.7769035696983337), ('##select', -0.07492552697658539), ('+', -0.5324431657791138), ('sleep', -0.16066639125347137), ('%', -0.27638185024261475), ('2815', -0.22623951733112335), ('%', -0.3051098883152008), ('29', -0.6818872094154358), ('+', -0.9565802216529846), ('%', -0.2550828754901886), ('29', -0.654218316078186), ('+', -0.38261333107948303), ('-', -0.0908629298210144), ('-', -0.1018875390291214), ('+', -0.4557470381259918), ('/', -0.14139120280742645), ('category',

66 - SQL Injection
[('[CLS]', -0.0), ('get', -0.005680008325725794), ('/', -0.008814548142254353), ('blog', -0.006326097063720226), ('/', -0.0080677829682827), ('index', -0.002941365586593747), ('.', -0.008778941817581654), ('php', -0.0004883938818238676), ('/', -0.006598559208214283), ('search', -0.0), ('/', -0.012338455766439438), ('percentage', -0.0006044995971024036), ('%', -0.12009094655513763), ('22', -1.0), ('[SEP]', -0.0014187282649800181)]


66 - SQL Injection
[('[CLS]', -0.0), ('get', -0.07119303941726685), ('/', -0.0955895334482193), ('blog', -0.005172796547412872), ('/', -0.14096057415008545), ('index', -0.0025114722084254026), ('.', -0.0011810321593657136), ('php', -0.0015077320858836174), ('/', -0.10363814979791641), ('2020', -0.005587780382484198), ('/', -0.11136897653341293), ('03', -0.01276936661452055), ('/', -0.08520158380270004), ('23', -0.005404212977737188), ('/', -0.06435585767030716), ('fu', -0.0006444344180636108), ('##ga', -0.0002889465249609202), ('-', -0.003351396881043911), ('aut', -0.00015821386477909982), ('-', -0.0023800742346793413), ('rec', -0.0007100612856447697), ('##usa', -0.00021883021690882742), ('##nd', -0.0013715705135837197), ('##ae', -0.0018132071709260345), ('-', -0.0027051696088165045), ('sed', -0.00025903424830175936), ('-', -0.0022612109314650297), ('dol', -0.0), ('##or', -0.0009711449383758008), ('-', -0.004164888057857752), ('qu', -0.0008831293671391904), ('##ia', -0.0187544468790292

In [19]:
OS_Command_Injection = pd.read_csv('/content/gdrive/MyDrive/Code_Injection_Dataset/data_new/88.csv')
for index, row in OS_Command_Injection.iterrows():
    if index > 10:
        break
    # if index <= 1000:
    #     continue
    text_batch = [row['text']]
    encoding = tokenizer(text_batch, return_tensors='pt')
    input_ids = encoding['input_ids'].to("cuda")
    attention_mask = encoding['attention_mask'].to("cuda")
    token_type_ids = encoding['token_type_ids'].to("cuda")
    # true class is positive - 1
    true_class = 0
    # generate an explanation for the input
    expl = explanations.generate_LRP(input_ids=input_ids, attention_mask=attention_mask, start_layer=0)[0]
    # normalize scores
    expl = (expl - expl.min()) / (expl.max() - expl.min())
    # get the model classification
    output = torch.nn.functional.softmax(model(input_ids=input_ids, attention_mask=attention_mask)[0], dim=-1)
    classification = output.argmax(dim=-1).item()
    # get class name
    class_name = classifications[classification]
    print(class_name)
    # if the classification is negative, higher explanation scores are more negative
    # flip for visualization
    if class_name != "000 - Normal":
      expl *= (-1)

    tokens = tokenizer.convert_ids_to_tokens(input_ids.flatten())
    print([(tokens[i], expl[i].item()) for i in range(len(tokens))])
    vis_data_records = [visualization.VisualizationDataRecord(
                                    expl,
                                    output[0][classification],
                                    classification,
                                    true_class,
                                    true_class,
                                    1,
                                    tokens,
                                    1)]
    visualization.visualize_text(vis_data_records)

/usr/local/lib/python3.10/dist-packages/transformers/modeling_utils.py:962: FutureWarning: The `device` argument is deprecated and will be removed in v5 of Transformers.
  warnings.warn(


88 - OS Command Injection
[('[CLS]', -0.0), ('post', -0.036510709673166275), ('/', -0.02298114262521267), ('cgi', -0.13898004591464996), ('-', -0.07782929390668869), ('bin', -0.09881580621004105), ('/', -0.032990437000989914), ('view', -0.03840689733624458), ('##log', -0.07504184544086456), ('.', -0.0857972651720047), ('asp', -0.08860279619693756), ('remote', -0.12054913491010666), ('_', -0.14311356842517853), ('submit', -0.06254799664020538), ('_', -0.2607456147670746), ('flag', -0.457491397857666), ('=', -0.4046490788459778), ('1', -0.6752930283546448), ('&', -0.6657512187957764), ('remote', -0.0795556828379631), ('_', -0.0917825773358345), ('syslog', -0.01538124866783619), ('_', -0.11291085928678513), ('flag', -0.15484945476055145), ('=', -0.23205530643463135), ('1', -0.16333827376365662), ('&', -0.32565176486968994), ('remote', -0.08132412284612656), ('##sys', -0.029736341908574104), ('##logs', -0.007070241030305624), ('##upport', -0.015950007364153862), ('##ed', -0.043408282101154

000 - Normal
[('[CLS]', 0.0), ('post', 0.7518270611763), ('/', 0.41034966707229614), ('<', 1.0), ('?', 0.3201042711734772), ('xml', 0.15861989557743073), ('version', 0.1781313419342041), ('=', 0.17633843421936035), ('"', 0.16288994252681732), ('1', 0.42688775062561035), ('.', 0.08327068388462067), ('0', 0.16144424676895142), ('"', 0.006609341595321894), ('encoding', 0.01229253038764), ('=', 0.044432640075683594), ('"', 0.026195283979177475), ('utf', 0.0073386593721807), ('-', 0.05847301706671715), ('8', 0.0), ('"', 0.024209922179579735), ('?', 0.03088044933974743), ('>', 0.1172904521226883), ('[SEP]', 0.0644221380352974)]


126 - Path Traversal
[('[CLS]', -0.0), ('get', -0.03599589318037033), ('/', -0.003302957396954298), ('tiki', -0.011236783117055893), ('-', -0.004134604707360268), ('list', -0.004835259169340134), ('##mov', -0.0), ('##ies', -0.0032889985013753176), ('.', -0.013672958128154278), ('php', -0.007871379144489765), ('?', -0.029437506571412086), ('movie', -0.007079726550728083), ('=', -0.07247348129749298), ('.', -0.8692660331726074), ('.', -1.0), ('/', -0.1943029761314392), ('.', -0.5444626808166504), ('.', -0.6331731081008911), ('/', -0.2524500787258148), ('.', -0.6210674047470093), ('.', -0.7450751066207886), ('/', -0.2514919936656952), ('.', -0.41498756408691406), ('.', -0.5243656039237976), ('/', -0.19647663831710815), ('.', -0.5983653664588928), ('.', -0.5945327281951904), ('/', -0.23534990847110748), ('.', -0.5264410376548767), ('.', -0.5887405872344971), ('/', -0.1218104213476181), ('etc', -0.06384401768445969), ('/', -0.034563396126031876), ('passwd', -0.03047502413392067), ('%', -0.0

126 - Path Traversal
[('[CLS]', -0.0), ('get', -0.5162922143936157), ('/', -0.13787397742271423), ('?', -1.0), ('p4', -0.22458846867084503), ('##yl', -0.2677673101425171), ('##04', -0.004400841426104307), ('##d', -0.034082576632499695), ('=', -0.396136611700058), ('.', -0.33339202404022217), ('.', -0.40341928601264954), ('/', -0.2107623666524887), ('.', -0.29816508293151855), ('.', -0.3439398407936096), ('/', -0.1850043535232544), ('.', -0.2906133532524109), ('.', -0.34103095531463623), ('/', -0.15975354611873627), ('.', -0.21882781386375427), ('.', -0.21128278970718384), ('/', -0.1587165743112564), ('.', -0.17227190732955933), ('.', -0.14642420411109924), ('/', -0.1027686595916748), ('.', -0.09855839610099792), ('.', -0.09695360064506531), ('/', -0.08895694464445114), ('.', -0.08747555315494537), ('.', -0.07918496429920197), ('/', -0.06027885898947716), ('.', -0.050152525305747986), ('.', -0.04315292090177536), ('/', -0.05266359820961952), ('.', -0.05257030576467514), ('.', -0.0556310

...

88 - OS Command Injection
[('[CLS]', -0.0), ('get', -0.01568751595914364), ('/', -0.0), ('index', -0.0450265072286129), ('.', -0.007559978403151035), ('php', -0.06507039070129395), ('?', -0.47335124015808105), ('s', -0.5099793076515198), ('=', -1.0), ('/', -0.08427534252405167), ('module', -0.07322856038808823), ('/', -0.026339204981923103), ('action', -0.011835016310214996), ('/', -0.01862136833369732), ('param1', -0.022468842566013336), ('/', -0.08863159269094467), ('$', -0.10648693889379501), ('{', -0.2013774812221527), ('@', -0.10226818919181824), ('die', -0.06498230248689651), ('(', -0.01112582441419363), ('sha1', -0.07656633108854294), ('(', -0.0121877770870924), ('xyz', -0.014644108712673187), ('##t', -0.06468722224235535), (')', -0.22003896534442902), (')', -0.295232355594635), ('}', -0.6341002583503723), ('[SEP]', -0.024123165756464005)]


126 - Path Traversal
[('[CLS]', -0.0), ('post', -0.5813283920288086), ('/', -0.13024671375751495), ('blog', -0.10472672432661057), ('/', -0.14725783467292786), ('index', -0.17193379998207092), ('.', -0.15154142677783966), ('php', -0.11736545711755753), ('/', -0.39461851119995117), ('my', -0.40232905745506287), ('-', -0.08880025148391724), ('account', -0.48405614495277405), ('/', -0.17776620388031006), ('edit', -0.2755574584007263), ('-', -0.14765030145645142), ('password', -0.4509125053882599), ('/', -0.31685513257980347), ('password', -0.404267281293869), ('_', -0.2513118088245392), ('current', -0.9166040420532227), ('=', -0.9568890929222107), ('%', -0.5974215865135193), ('2f', -0.5041408538818359), ('##etc', -0.7503136992454529), ('%', -0.5116680264472961), ('2f', -0.22024483978748322), ('##pass', -0.16066037118434906), ('##wd', -0.5033236742019653), ('&', -0.3252129554748535), ('password', -0.3413885533809662), ('_', -0.18071188032627106), ('1', -1.0), ('=', -0.4186599552631378), ('

126 - Path Traversal
[('[CLS]', -0.0), ('post', -0.5708025693893433), ('/', -0.12946277856826782), ('blog', -0.08560929447412491), ('/', -0.15733671188354492), ('index', -0.15347644686698914), ('.', -0.11832805722951889), ('php', -0.12439453601837158), ('/', -0.42170339822769165), ('my', -0.3218754827976227), ('-', -0.06494994461536407), ('account', -0.4123857319355011), ('/', -0.17268358170986176), ('edit', -0.23581524193286896), ('-', -0.11325587332248688), ('password', -0.3038922846317291), ('/', -0.18064013123512268), ('password', -0.2889137268066406), ('_', -0.1611769199371338), ('current', -0.6926820278167725), ('=', -0.8710812330245972), ('.', -1.0), ('.', -0.9589641690254211), ('%', -0.544462263584137), ('2f', -0.3833312392234802), ('.', -0.5526250004768372), ('.', -0.5933496952056885), ('%', -0.34325385093688965), ('2f', -0.3373301327228546), ('.', -0.5015627145767212), ('.', -0.4895140826702118), ('%', -0.23009082674980164), ('2f', -0.21812230348587036), ('.', -0.362376064062

126 - Path Traversal
[('[CLS]', -0.0), ('post', -0.6911203265190125), ('/', -0.14988437294960022), ('blog', -0.07802516967058182), ('/', -0.15688835084438324), ('index', -0.1870437115430832), ('.', -0.11948725581169128), ('php', -0.15750235319137573), ('/', -0.38783296942710876), ('my', -0.3804854154586792), ('-', -0.0633777379989624), ('account', -0.35456937551498413), ('/', -0.16604772210121155), ('edit', -0.26479098200798035), ('-', -0.12201360613107681), ('password', -0.39614251255989075), ('/', -0.25016531348228455), ('password', -0.3644171953201294), ('_', -0.23322008550167084), ('current', -1.0), ('=', -0.9954517483711243), ('%', -0.50432950258255), ('2f', -0.25279033184051514), ('.', -0.48462313413619995), ('.', -0.516346275806427), ('%', -0.40563586354255676), ('2f', -0.4007784426212311), ('.', -0.45791903138160706), ('.', -0.44937077164649963), ('%', -0.2509065866470337), ('2f', -0.20621363818645477), ('.', -0.3101233243942261), ('.', -0.312315434217453), ('%', -0.17118199169

126 - Path Traversal
[('[CLS]', -0.0), ('post', -0.7697655558586121), ('/', -0.20414231717586517), ('blog', -0.10404159873723984), ('/', -0.2171815186738968), ('index', -0.251635879278183), ('.', -0.17199455201625824), ('php', -0.19721969962120056), ('/', -0.46195435523986816), ('my', -0.3530474603176117), ('-', -0.14672516286373138), ('account', -0.5299288034439087), ('/', -0.25610411167144775), ('edit', -0.300335168838501), ('-', -0.22651608288288116), ('password', -0.4671148359775543), ('/', -0.3967509865760803), ('password', -0.445527583360672), ('_', -0.31833094358444214), ('current', -0.9065327644348145), ('=', -0.9711892008781433), ('etc', -1.0), ('%', -0.5566552877426147), ('2f', -0.3197660744190216), ('##pass', -0.5714033246040344), ('##wd', -0.8643445372581482), ('&', -0.3695789873600006), ('password', -0.3767663836479187), ('_', -0.2323547899723053), ('1', -0.9103450775146484), ('=', -0.39951199293136597), ('q', -0.36109989881515503), ('##lh', -0.11005830764770508), ('##or',

In [20]:
for index, row in normal.iterrows():
    text_batch = [row['text']]
    encoding = tokenizer(text_batch, return_tensors='pt')
    input_ids = encoding['input_ids'].to("cuda")
    attention_mask = encoding['attention_mask'].to("cuda")
    token_type_ids = encoding['token_type_ids'].to("cuda")
    # true class is positive - 1
    true_class = 0



    # get the model classification
    output = torch.nn.functional.softmax(model(input_ids=input_ids, attention_mask=attention_mask)[0], dim=-1)
    classification = output.argmax(dim=-1).item()
    # get class name
    class_name = classifications[classification]

    # if the classification is negative, higher explanation scores are more negative
    # flip for visualization
    if class_name != "000 - Normal":
        # generate an explanation for the input
        expl = explanations.generate_LRP(input_ids=input_ids, attention_mask=attention_mask, start_layer=0)[0]
        # normalize scores
        expl = (expl - expl.min()) / (expl.max() - expl.min())
        expl *= (-1)
        tokens = tokenizer.convert_ids_to_tokens(input_ids.flatten())
        print([(tokens[i], expl[i].item()) for i in range(len(tokens))])
        vis_data_records = [visualization.VisualizationDataRecord(
                                        expl,
                                        output[0][classification],
                                        classification,
                                        true_class,
                                        true_class,
                                        1,
                                        tokens,
                                        1)]
        visualization.visualize_text(vis_data_records)
    else:
        count += 1
print("Acc: ",count/(index + 1))

[('[CLS]', -0.0), ('get', -0.10455641150474548), ('/', -0.04592742770910263), ('blog', -0.009303351864218712), ('/', -0.05676612630486488), ('xmlrpc', -0.012265663594007492), ('.', -0.0069597079418599606), ('php', -0.0), ('?', -0.09950719028711319), ('rs', -0.30921003222465515), ('##d', -1.0), ('[SEP]', -0.004829986020922661)]


[('[CLS]', -0.0), ('get', -0.9763017892837524), ('/', -0.08352572470903397), ('blog', -0.0978754460811615), ('/', -0.09634345769882202), ('wp', -0.06121765077114105), ('-', -0.02896225079894066), ('includes', -0.08687219023704529), ('/', -0.02182754874229431), ('css', -0.0660860538482666), ('/', -0.02671397291123867), ('admin', -0.029452981427311897), ('-', -0.0), ('bar', -0.09759624302387238), ('.', -0.14666497707366943), ('min', -0.6297728419303894), ('.', -0.09920357167720795), ('css', -0.4243278503417969), ('?', -0.3823866844177246), ('ver', -0.38111987709999084), ('=', -1.0), ('4', -0.5657293796539307), ('.', -0.09452962130308151), ('9', -0.06609194725751877), ('.', -0.0696585476398468), ('5', -0.19839254021644592), ('[SEP]', -0.1766037493944168)]


[('[CLS]', -0.0), ('get', -0.3697129786014557), ('/', -0.024935899302363396), ('blog', -0.01720277965068817), ('/', -0.03302156925201416), ('wp', -0.021181626245379448), ('-', -0.008905954658985138), ('content', -0.020449198782444), ('/', -0.011977922171354294), ('plugins', -0.014865824952721596), ('/', -0.003068698337301612), ('user', -0.003730956232175231), ('-', -0.0031311605125665665), ('registration', -0.0021374498028308153), ('/', -0.006117644254118204), ('assets', -0.008435599505901337), ('/', -0.006128772161900997), ('css', -0.008803167380392551), ('/', -0.0026556020602583885), ('user', -0.0011070538312196732), ('-', -0.0021156934089958668), ('registration', -0.0), ('.', -0.01720399782061577), ('css', -0.12206488102674484), ('?', -0.4275641143321991), ('ver', -0.4279260039329529), ('=', -1.0), ('1', -0.611284613609314), ('.', -0.19820831716060638), ('8', -0.7318464517593384), ('.', -0.08112002909183502), ('2', -0.05925385281443596), ('.', -0.1137838140130043), ('1', -0.44877454

[('[CLS]', -0.0), ('get', -0.16682176291942596), ('/', -0.014888717792928219), ('blog', -0.020806245505809784), ('/', -0.0254687387496233), ('wp', -0.046977315098047256), ('-', -0.0033447593450546265), ('content', -0.044668048620224), ('/', -0.015276612713932991), ('themes', -0.08120503276586533), ('/', -0.004778342321515083), ('twenty', -0.0037204979453235865), ('##sevent', -0.0), ('##een', -0.0075932457111775875), ('/', -0.0022975895553827286), ('style', -0.04116959124803543), ('.', -0.015838034451007843), ('css', -0.36764344573020935), ('?', -0.18220382928848267), ('ver', -0.27945810556411743), ('=', -1.0), ('4', -0.6650790572166443), ('.', -0.08937589079141617), ('9', -0.12068856507539749), ('.', -0.07601857930421829), ('5', -0.22190657258033752), ('[SEP]', -0.13426055014133453)]


[('[CLS]', -0.0), ('get', -0.9941031336784363), ('/', -0.18024395406246185), ('blog', -0.06771282851696014), ('/', -0.17396339774131775), ('wp', -0.06832221895456314), ('-', -0.07930836826562881), ('includes', -0.01897016167640686), ('/', -0.10690377652645111), ('js', -0.1427893489599228), ('/', -0.0659019872546196), ('jquery', -0.01601499877870083), ('/', -0.05611294507980347), ('jquery', -0.0), ('-', -0.049698811024427414), ('migrate', -0.0011676405556499958), ('.', -0.12673844397068024), ('min', -0.09830378741025925), ('.', -0.1430116444826126), ('js', -0.12392082810401917), ('?', -0.5274823904037476), ('ver', -0.3240637183189392), ('=', -0.862614095211029), ('1', -1.0), ('.', -0.2169908583164215), ('4', -0.23345211148262024), ('.', -0.16033902764320374), ('1', -0.24214425683021545), ('[SEP]', -0.21678794920444489)]


...

[('[CLS]', -0.0), ('get', -0.05893580988049507), ('/', -0.012749692425131798), ('blog', -0.01013149693608284), ('/', -0.009264444932341576), ('index', -0.0036008853930979967), ('.', -0.01707710698246956), ('php', -0.0), ('/', -0.005453165154904127), ('page', -0.0015506751369684935), ('/', -0.013470376841723919), ('?', -0.15657514333724976), ('s', -1.0), ('[SEP]', -0.013828149996697903)]


[('[CLS]', -0.0), ('get', -0.05893580988049507), ('/', -0.012749692425131798), ('blog', -0.01013149693608284), ('/', -0.009264444932341576), ('index', -0.0036008853930979967), ('.', -0.01707710698246956), ('php', -0.0), ('/', -0.005453165154904127), ('page', -0.0015506751369684935), ('/', -0.013470376841723919), ('?', -0.15657514333724976), ('s', -1.0), ('[SEP]', -0.013828149996697903)]


[('[CLS]', -0.0), ('get', -0.05893580988049507), ('/', -0.012749692425131798), ('blog', -0.01013149693608284), ('/', -0.009264444932341576), ('index', -0.0036008853930979967), ('.', -0.01707710698246956), ('php', -0.0), ('/', -0.005453165154904127), ('page', -0.0015506751369684935), ('/', -0.013470376841723919), ('?', -0.15657514333724976), ('s', -1.0), ('[SEP]', -0.013828149996697903)]


[('[CLS]', -0.0), ('post', -1.0), ('/', -0.15301407873630524), ('blog', -0.05635419115424156), ('/', -0.6866226196289062), ('registration', -0.5483770370483398), ('/', -0.34603533148765564), ('registration', -0.7607446908950806), ('first', -0.4526025354862213), ('_', -0.15003135800361633), ('name', -0.04955568164587021), ('=', -0.3128149211406708), ('zap', -0.19874680042266846), ('&', -0.16901443898677826), ('user', -0.04639715328812599), ('_', -0.06249067932367325), ('login', -0.03447915241122246), ('=', -0.17977167665958405), ('spirit', -0.011982990428805351), ('##ed', -0.02926621586084366), ('##bus', -0.008846037089824677), ('##ta', -0.02039949968457222), ('##rd', -0.044120315462350845), ('##7', -0.04461405426263809), ('&', -0.1016509011387825), ('user', -0.0142360283061862), ('_', -0.009348850697278976), ('pass', -0.042684897780418396), ('=', -0.08601905405521393), ('zap', -0.05690361186861992), ('&', -0.0950663760304451), ('user', -0.011028699576854706), ('_', -0.02029522880911827

Acc:  0.9764529740029945


In [21]:
for index, row in sqli.iterrows():
    text_batch = [row['text']]
    encoding = tokenizer(text_batch, return_tensors='pt')
    input_ids = encoding['input_ids'].to("cuda")
    attention_mask = encoding['attention_mask'].to("cuda")
    token_type_ids = encoding['token_type_ids'].to("cuda")
    # true class is positive - 1
    true_class = 0



    # get the model classification
    output = torch.nn.functional.softmax(model(input_ids=input_ids, attention_mask=attention_mask)[0], dim=-1)
    classification = output.argmax(dim=-1).item()
    # get class name
    class_name = classifications[classification]

    # if the classification is negative, higher explanation scores are more negative
    # flip for visualization
    if class_name != "66 - SQL Injection":
        # generate an explanation for the input
        expl = explanations.generate_LRP(input_ids=input_ids, attention_mask=attention_mask, start_layer=0)[0]
        # normalize scores
        expl = (expl - expl.min()) / (expl.max() - expl.min())
        expl *= (-1)
        tokens = tokenizer.convert_ids_to_tokens(input_ids.flatten())
        print([(tokens[i], expl[i].item()) for i in range(len(tokens))])
        vis_data_records = [visualization.VisualizationDataRecord(
                                        expl,
                                        output[0][classification],
                                        classification,
                                        true_class,
                                        true_class,
                                        1,
                                        tokens,
                                        1)]
        visualization.visualize_text(vis_data_records)
    else:
        count += 1
print("Acc: ",count/(index + 1))

[('[CLS]', -0.0), ('post', -0.09275215864181519), ('/', -0.006543833762407303), ('blog', -0.009949390776455402), ('/', -0.014908256940543652), ('wp', -0.02982264570891857), ('-', -0.02081940323114395), ('login', -0.03916158899664879), ('.', -0.13298165798187256), ('php', -0.06858418136835098), ('log', -0.7302045822143555), ('=', -0.20685622096061707), ('shame', -0.07532907277345657), ('##ful', -0.023549294099211693), ('##pl', -0.01270012091845274), ('##over', -0.011996445246040821), ('##3', -0.06745666265487671), ('&', -0.07185939699411392), ('pwd', -0.16938446462154388), ('=', -0.15860871970653534), ('$', -0.09308996796607971), ('aq', -0.025246577337384224), ('##lb', -0.017105260863900185), ('##4h', -0.02056165412068367), ('&', -0.03207278996706009), ('remember', -0.012583998031914234), ('##me', -0.02787892334163189), ('=', -0.05702807009220123), ('forever', -0.024922117590904236), ('&', -0.021060343831777573), ('wp', -0.00922305416315794), ('-', -0.0067596822045743465), ('submit', -0

[('[CLS]', -0.0), ('get', -1.0), ('/', -0.07892885059118271), ('blog', -0.06524556130170822), ('/', -0.07152130454778671), ('wp', -0.05695578083395958), ('-', -0.010724684223532677), ('includes', -0.04245031997561455), ('/', -0.028029344975948334), ('js', -0.042056769132614136), ('/', -0.011558464728295803), ('api', -0.04368921369314194), ('-', -0.0), ('request', -0.015661610290408134), ('.', -0.09342340379953384), ('min', -0.07855740934610367), ('.', -0.08117298036813736), ('js', -0.2273312509059906), ('?', -0.29091453552246094), ('ver', -0.1931178867816925), ('=', -0.30277013778686523), ('4', -0.7404473423957825), ('.', -0.0968705341219902), ('9', -0.10569773614406586), ('.', -0.052023231983184814), ('5', -0.1364009529352188), ('[SEP]', -0.06295640021562576)]


[('[CLS]', -0.0), ('get', -1.0), ('/', -0.19087496399879456), ('blog', -0.13372059166431427), ('/', -0.2006138563156128), ('index', -0.12412097305059433), ('.', -0.13581670820713043), ('php', -0.15856118500232697), ('/', -0.3003242611885071), ('my', -0.20004798471927643), ('-', -0.24676896631717682), ('account', -0.11100706458091736), ('/', -0.13241547346115112), ('edit', -0.04314292222261429), ('-', -0.2008064091205597), ('profile', -0.03295307978987694), ('/', -0.07558874040842056), ('post', -0.08274737000465393), ('.', -0.16187702119350433), ('php', -0.12882354855537415), ('/', -0.849801778793335), ('?', -0.05565442144870758), ('action', -0.11320190131664276), ('=', -0.03768504038453102), ('edit', -0.01797555759549141), ('&', -0.03463604673743248), ('post', -0.03204728662967682), ('=', -0.03913480415940285), ('%', -0.008419742807745934), ('7b', -0.00999209564179182), ('%', -0.02005414478480816), ('7b', -0.0056474716402590275), ('%', -0.016700364649295807), ('20', -0.0008256011642515

[('[CLS]', -0.0), ('get', -0.4110643267631531), ('/', -0.1057591438293457), ('blog', -0.057825442403554916), ('/', -0.13615894317626953), ('wp', -0.030472559854388237), ('-', -0.01390029489994049), ('login', -0.014770480804145336), ('.', -0.06636690348386765), ('php', -0.022401053458452225), ('?', -0.13420595228672028), ('_', -0.09313711524009705), ('wp', -0.02684292197227478), ('##non', -0.0), ('##ce', -0.10115943849086761), ('=', -0.3426070213317871), ('7d', -0.3444865643978119), ('##e0a', -0.0045331199653446674), ('##bc', -0.009083276614546776), ('##dc', -0.0015652263537049294), ('##2', -0.017942706122994423), ('&', -0.023422714322805405), ('action', -0.021704163402318954), ('=', -0.085227832198143), ('logout', -1.0), ('[SEP]', -0.021454768255352974)]


[('[CLS]', -0.0), ('get', -1.0), ('/', -0.10825512558221817), ('blog', -0.030592145398259163), ('/', -0.09800250828266144), ('wp', -0.04085531085729599), ('-', -0.02342732809484005), ('admin', -0.045216239988803864), ('/', -0.07218347489833832), ('load', -0.013377677649259567), ('-', -0.01648673415184021), ('styles', -0.0052050151862204075), ('.', -0.03062801994383335), ('php', -0.06971167027950287), ('?', -0.08121009171009064), ('c', -0.13474880158901215), ('=', -0.08570680022239685), ('0', -0.01196060050278902), ('&', -0.007191381882876158), ('dir', -0.00728945154696703), ('=', -0.015197720378637314), ('lt', -0.0005524881416931748), ('##r', -0.006153002381324768), ('&', -0.0068434057757258415), ('load', -0.018210940062999725), ('%', -0.34200218319892883), ('5b', -0.0097882691770792), ('%', -0.01558424811810255), ('5d', -0.0008018722874112427), ('=', -0.004680661018937826), ('dash', -0.003993725869804621), ('##icon', -0.0011344164377078414), ('##s', -0.006654675584286451), (',', -0.01

...

[('[CLS]', -0.0), ('get', -1.0), ('/', -0.0365511029958725), ('blog', -0.07682431489229202), ('/', -0.0462808683514595), ('wp', -0.09679610282182693), ('-', -0.03455071896314621), ('includes', -0.03677088022232056), ('/', -0.021239925175905228), ('js', -0.13567212224006653), ('/', -0.008786874823272228), ('plupload', -0.03580410033464432), ('/', -0.0), ('moxie', -0.008469619788229465), ('.', -0.09534209221601486), ('min', -0.10531317442655563), ('.', -0.04652637615799904), ('js', -0.15352630615234375), ('?', -0.3250334560871124), ('ver', -0.27855804562568665), ('=', -0.4995530843734741), ('1', -0.7173830270767212), ('.', -0.09976489841938019), ('3', -0.09762997925281525), ('.', -0.1100931167602539), ('5', -0.2623867094516754), ('[SEP]', -0.10436497628688812)]


[('[CLS]', -0.0), ('post', -0.14483758807182312), ('/', -0.03723566606640816), ('blog', -0.0335669182240963), ('/', -0.049578357487916946), ('index', -0.03757147863507271), ('.', -0.03660888597369194), ('php', -0.06667604297399521), ('/', -0.062232062220573425), ('my', -0.06876596063375473), ('-', -0.013328781351447105), ('account', -0.06385669857263565), ('/', -0.02546340599656105), ('edit', -0.01660550944507122), ('-', -0.009148591198027134), ('profile', -0.0271516814827919), ('/', -0.013164692558348179), ('profile', -0.006556031294167042), ('-', -0.01107693836092949), ('pic', -0.03219064697623253), ('-', -0.012214086949825287), ('url', -0.05835706740617752), ('=', -0.1207001581788063), ('&', -0.04234318435192108), ('profile', -0.00830647349357605), ('-', -0.006119173485785723), ('default', -0.008846004493534565), ('-', -0.01103636808693409), ('image', -0.826880156993866), ('=', -0.05287305638194084), ('http', -0.11348439007997513), ('%', -0.03174296021461487), ('3a', -0.008707109838

[('[CLS]', -0.0), ('get', -1.0), ('/', -0.26390141248703003), ('blog', -0.0591760016977787), ('/', -0.1916600614786148), ('wp', -0.05703841894865036), ('-', -0.13842201232910156), ('includes', -0.01498599536716938), ('/', -0.23527774214744568), ('css', -0.033405061811208725), ('/', -0.06850660592317581), ('dash', -0.05050240457057953), ('##icon', -0.029546841979026794), ('##s', -0.011777110397815704), ('.', -0.09516126662492752), ('min', -0.012143818661570549), ('.', -0.058810487389564514), ('css', -0.0), ('?', -0.020066197961568832), ('ver', -0.0173394363373518), ('=', -0.008296334184706211), ('4', -0.0568123534321785), ('.', -0.07379724830389023), ('9', -0.03549713268876076), ('.', -0.08772610127925873), ('5', -0.02843439020216465), ('[SEP]', -0.02286391705274582)]


[('[CLS]', -0.0), ('get', -0.6417820453643799), ('/', -0.02163918875157833), ('blog', -0.036295197904109955), ('/', -0.03433213382959366), ('wp', -0.07106879353523254), ('-', -0.013247211463749409), ('includes', -0.046668533235788345), ('/', -0.010060972534120083), ('js', -0.07708955556154251), ('/', -0.0), ('utils', -0.05834557116031647), ('.', -0.09161236882209778), ('min', -0.15165483951568604), ('.', -0.049288567155599594), ('js', -0.32132628560066223), ('?', -0.1926134079694748), ('ver', -0.19489000737667084), ('=', -1.0), ('4', -0.589769721031189), ('.', -0.08174782991409302), ('9', -0.07083825767040253), ('.', -0.02414715476334095), ('5', -0.22771325707435608), ('[SEP]', -0.12940272688865662)]


Acc:  1.930905695611578
